## 语言模型数据集（周杰伦专辑歌词）

接下来我们介绍如何预处理一个语言模型数据集，并将其转换成字符级循环神经网络所需要的输入格式。为此，我们收集了周杰伦从第一张专辑《Jay》到第十张专辑《跨时代》中的歌词，应用循环神经网络来训练一个语言模型。当模型训练好后，我们就可以用这个模型来创作歌词。

In [1]:
# read data
import tensorflow as tf
import random
import zipfile
import numpy as np
with zipfile.ZipFile('./data/jaychou_lyrics.txt.zip') as zin:
    with zin.open('jaychou_lyrics.txt') as f:
        corpus_chars = f.read().decode('utf-8')

# show
corpus_chars[:80]


'想要有直升机\n想要和你飞到宇宙去\n想要和你融化在一起\n融化在宇宙里\n我每天每天每天在想想想想著你\n这样的甜蜜\n让我开始乡相信命运\n感谢地心引力\n让我碰到你\n漂亮'

### 这个数据集有6万多个字符。为了打印方便，我们把换行符替换成空格，然后仅使用前1万个字符来训练模型。

In [2]:
corpus_chars = corpus_chars.replace('\n',' ').replace('\r',' ')
corpus_chars = corpus_chars[0:10000]
len(corpus_chars)

10000

### 建立字符索引
我们将每个字符映射成一个从0开始的连续整数，又称索引，来方便之后的数据处理。为了得到索引，我们将数据集里所有不同字符取出来，然后将其逐一映射到索引来构造词典。接着，打印vocab_size，即词典中不同字符的个数，又称词典大小。

In [3]:
idx_to_char = list(set(corpus_chars))
char_to_idx = dict([(char,i) for i , char in enumerate(idx_to_char)])
vocab_size = len(char_to_idx)
vocab_size

1027

In [4]:
corpus_indices = [char_to_idx[char] for char in corpus_chars]
sample = corpus_indices[:26]
print('chars: ',"".join([idx_to_char[idx] for idx in sample]))


chars:  想要有直升机 想要和你飞到宇宙去 想要和你融化在一起


In [5]:
# 隨機採樣, 每次隨機採一個 批量大小來做訓練, # utils
def data_iter_random(corpus_indices, batch_size, num_steps,ctx= None):
    # -1,輸出索引相應輸入索引+1
    num_examples = (len(corpus_indices) -1) // num_steps
    print("num_example: \n",num_examples)
    epoch_size = num_examples // batch_size
    example_indices = list(range(num_examples))
    random.shuffle(example_indices)
    
    def _data(pos):
        return corpus_indices[pos: pos + num_steps]
    
    for i in range(epoch_size):
        # read  random sample which size is batch_size once
        i = i * batch_size
        batch_indices = example_indices[i: i + batch_size]
        X = [_data(j * num_steps) for j in batch_indices]
        Y = [_data(j * num_steps + 1) for j in batch_indices]
        yield np.array(X,ctx), np.array(Y,ctx)
        


In [6]:
# test 相邻的两个随机小批量在原始序列上的位置不一定相毗邻。
my_seq = list(range(30))
for X, Y in data_iter_random(my_seq, batch_size=2, num_steps=6):
    print('X:',X , '\nY:',Y,'\n')

    

num_example: 
 4
X: [[ 0  1  2  3  4  5]
 [12 13 14 15 16 17]] 
Y: [[ 1  2  3  4  5  6]
 [13 14 15 16 17 18]] 

X: [[ 6  7  8  9 10 11]
 [18 19 20 21 22 23]] 
Y: [[ 7  8  9 10 11 12]
 [19 20 21 22 23 24]] 



In [7]:
# 相邻采样 utils
def data_iter_consecutive(corpus_indices, batch_size, num_steps, ctx=None):
    corpus_indices = np.array(corpus_indices)
    data_len = len(corpus_indices)
    batch_len = data_len // batch_size
    indices = corpus_indices[0:batch_size*batch_len].reshape((batch_size,batch_len))
    epoch_size = (batch_len - 1) //num_steps
    for i in range(epoch_size):
        i = i * num_steps
        X = indices[:,i: i + num_steps]
        Y = indices[:,i+1:i+num_steps+1]
        yield X, Y 

for X, Y in data_iter_consecutive(my_seq,batch_size=2, num_steps=6):
    print('X:', X,'\nY:',Y)
    

X: [[ 0  1  2  3  4  5]
 [15 16 17 18 19 20]] 
Y: [[ 1  2  3  4  5  6]
 [16 17 18 19 20 21]]
X: [[ 6  7  8  9 10 11]
 [21 22 23 24 25 26]] 
Y: [[ 7  8  9 10 11 12]
 [22 23 24 25 26 27]]


# 循环神经网络的从零开始实现

我们将从零开始实现一个基于字符级循环神经网络的语言模型，并在周杰伦专辑歌词数据集上训练一个模型来进行歌词创作。首先，我们读取周杰伦专辑歌词数据集：

In [8]:
# data load
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import backend as f
import numpy as np
import sys
import time
sys.path.append("..") 

def load_data_jay_lyrics():
    """加载周杰伦歌词数据集"""
    with zipfile.ZipFile('./data/jaychou_lyrics.txt.zip') as zin:
        with zin.open('jaychou_lyrics.txt') as f:
            corpus_chars = f.read().decode('utf-8')
    corpus_chars = corpus_chars.replace('\n', ' ').replace('\r', ' ')
    corpus_chars = corpus_chars[0:10000]
    idx_to_char = list(set(corpus_chars))
    char_to_idx = dict([(char, i) for i, char in enumerate(idx_to_char)])
    vocab_size = len(char_to_idx)
    corpus_indices = [char_to_idx[char] for char in corpus_chars]
    return corpus_indices, char_to_idx, idx_to_char, vocab_size

(corpus_indices, char_to_idx, idx_to_char, vocab_size) = load_data_jay_lyrics()

In [9]:
# one hot utils
def to_onehot(X,size):
     return [tf.one_hot(x,size,dtype=tf.float32) for x in X.T]

#test 
X = np.arange(10).reshape((2,5))
inputs = to_onehot(X,vocab_size)
len(inputs),inputs[0].shape

(5, TensorShape([2, 1027]))

In [10]:
# initial parameter
num_inputs, num_hiddens,num_outputs = vocab_size, 256, vocab_size

def get_params():
    def _one(shape):
        return tf.Variable(tf.random.normal(shape=shape,stddev=0.01,mean=0,dtype=tf.float32))

    # hidder layer
    W_xh = _one((num_inputs,num_hiddens))
    W_hh = _one((num_hiddens, num_hiddens))
    b_h = tf.Variable(tf.zeros(num_hiddens),dtype=tf.float32)

    #output layer
    W_hq = _one((num_hiddens, num_outputs))
    b_q = tf.Variable(tf.zeros(num_outputs), dtype=tf.float32)
    params = [W_xh, W_hh, b_h, W_hq, b_q]
    return params
    

In [11]:
# Define Model

## initail hidden  state
def init_rnn_state(batch_size, num_hiddens):
    return (tf.zeros(shape=(batch_size, num_hiddens)), )

# define caculate hidden state and output
def rnn(inputs, state, params):
    # inputs and outputs 皆為 num_steps個形狀為(batch_size, vocab_siez)的矩陣
    W_xh, W_hh, b_h, W_hq, b_q = params
    H, = state
    print((H,))
    outputs = []
    for X in inputs:
        X = tf.reshape(X,[-1,W_xh.shape[0]])
        H = tf.tanh(tf.matmul(X, W_xh) + tf.matmul(H, W_hh) + b_h)
        Y = tf.matmul(H,W_hq) + b_q
        outputs.append(Y)
    return outputs,(H,)

## TEST
state = init_rnn_state(X.shape[0], num_hiddens)
inputs = to_onehot(X, vocab_size)
params = get_params()
outputs, state_new = rnn(inputs,state,params)
print(len(outputs), outputs[0].shape, state_new[0].shape)

(<tf.Tensor: shape=(2, 256), dtype=float32, numpy=
array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0

In [12]:
# prefict 
def predict_rnn(prefix,num_chars, rnn, params, init_run_state, num_hiddens, vocab_size,
                idx_to_char, char_to_idx):
    state = init_rnn_state(1,num_hiddens)
    output = [char_to_idx[prefix[0]]]
    for t in range(num_chars + len(prefix) - 1):
        # 將上一時間步的輸出作為當前時間步輸入
        X = tf.convert_to_tensor(to_onehot(np.array([output[-1]]),vocab_size),dtype=tf.float32)
        print("before X ",X.shape)
        X = tf.reshape(X,[1,-1])
        print('\n reshape X ',X.shape)
        #計算輸出 跟 隱藏狀態
        (Y,state) = rnn(X, state, params)
        #下一個時間步的輸入是prefix里的字符或者當前的最佳預測字符
        if t < len(prefix) -1 :
            output.append(char_to_idx[prefix[t+1]])
        else:
            output.append(int(np.array(tf.argmax(Y[0],axis=1))))
    print(output)
    return ''.join([idx_to_char[i] for i in output]) 

#test
print(predict_rnn('分开',10,rnn,params,init_rnn_state, num_hiddens,vocab_size,idx_to_char, char_to_idx))


before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0.

# Clip gradient

循环神经网络中较容易出现梯度衰减或梯度爆炸。为了应对梯度爆炸，我们可以裁剪梯度（clip gradient）。假设我们把所有模型参数梯度的元素拼接成一个向量 $\boldsymbol{g}$，并设裁剪的阈值是$\theta$。裁剪后的梯度

$$ \min\left(\frac{\theta}{\|\boldsymbol{g}\|}, 1\right)\boldsymbol{g}$$

的$L_2$范数不超过$\theta$。

In [13]:
def grad_clipping(grads,theta):
    norm = np.array([0])
    for i in range(len(grads)):
        norm +=tf.math.reduce_sum(grads[i]**2)
    norm = np.sqrt(norm).item()
    new_gradient=[]
    if norm > theta:
        for grad in grads:
            new_gradient.append(grad * theta / norm)
    else:
        for grad in grads:
            new_gradient.append(grad)
    
    return new_gradient

    

In [14]:
# train function
import math


num_example: 
 285
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, num

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0.,

 285
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0.

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0.,

num_example: 
 285
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, num

...

       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
num_example: 
 285
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=flo

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0.,

       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
num_example: 
 285
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=flo

before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[ 0.6423943 , -0.9418873 , -0.99029166, -0.92381936, -0.9973487 ,
         0.7681015 , -0.922769  , -0.9781045 ,  0.89844704,  0.8260674 ,
         0.6717213 , -0.06079365,  0.9737755 ,  0.8100027 ,  0.96104413,
        -0.98539406, -0.89842254,  0.6641291 , -0.90210414,  0.84744424,
         0.9768851 ,  0.86403614, -0.8983979 , -0.18447734,  0.9811395 ,
        -0.9479789 ,  0.6693614 , -0.73029214,  0.97257197,  0.55049497,
        -0.96832645,  0.9770388 ,  0.7083078 ,  0.990802  ,  0.96287906,
         0.92937   ,  0.9318739 , -0.9918273 , -0.9639146 ,  0.95955473,
         0.959223  ,  0.9414424 , -0.9712005 ,  0.11398297,  0.92473954,
        -0.13053903,  0.95623255,  0.03186405,  0.9502554 , -0.67038274,
         0.78327227,  0.9880149 , -0.98088586,  0.98476696, -0.99631596,
         0.9762679 ,  0.9951091 , -0.9062204 , -0.9356017 , -0.61084145,
         0.96876186, -0.912928

before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[ 0.6423943 , -0.9418873 , -0.99029166, -0.92381936, -0.9973487 ,
         0.7681015 , -0.922769  , -0.9781045 ,  0.89844704,  0.82606727,
         0.6717213 , -0.06079366,  0.9737755 ,  0.8100027 ,  0.96104413,
        -0.98539406, -0.89842254,  0.6641291 , -0.90210396,  0.84744424,
         0.9768851 ,  0.86403614, -0.89839804, -0.18447734,  0.98113954,
        -0.9479789 ,  0.6693614 , -0.73029214,  0.97257197,  0.55049497,
        -0.96832645,  0.97703886,  0.7083079 ,  0.99080205,  0.96287906,
         0.92937   ,  0.93187386, -0.9918273 , -0.9639146 ,  0.95955473,
         0.959223  ,  0.9414425 , -0.97120047,  0.11398293,  0.9247395 ,
        -0.13053903,  0.95623255,  0.03186405,  0.9502556 , -0.67038274,
         0.7832721 ,  0.9880149 , -0.98088586,  0.98476696, -0.99631596,
         0.976268  ,  0.9951091 , -0.9062204 , -0.9356017 , -0.6108414 ,
         0.96876186, -0.912928

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[ 0.00086114,  0.01485544,  0.0094122 , ..., -0.012033  ,
        -0.00782276, -0.0048512 ],
       [ 0.00797421, -0.00472172, -0.00958318, ...,  0.00356867,
         0.0067425 ,  0.00529766],
       [-0.01265394,  0.00158982,  0.00652154, ..., -0.00208396,
        -0.00314704, -0.0045434 ],
       ...,
       [ 0.01200818, -0.02120439,  0.00029531, ...,  0.01071123,
        -0.00837339,  0.01246467],
       [-0.01860855,  0.00994494,  0.01605681, ..., -0.01357301,
        -0.00786264, -0.00770388],
       [ 0.00610579,  0.00662693,  0.00089762, ..., -0.00403852,
         0.00085939, -0.01666576]], dtype=float32)>,)
(<tf.T

         0.00063393,  0.00037094]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.0018588 ,  0.05188934, -0.05188382, ..., -0.02932087,
         0.00066883,  0.00546882],
       [-0.018019  ,  0.02249464, -0.08124015, ..., -0.02502952,
         0.00034121, -0.00313853],
       [-0.01469006,  0.06826554, -0.0768865 , ..., -0.02043809,
        -0.01655639, -0.00273468],
       ...,
       [-0.00049478,  0.04009033, -0.06836784, ..., -0.02816134,
        -0.01061648,  0.01263962],
       [-0.01662881,  0.03475684, -0.08545797, ..., -0.02633335,
        -0.01182601,  0.00096711],
       [ 0.00140272,  0.02787747, -0.0702765 , ..., -0.01818838,
        -0.0029871 ,  0.02054625]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.01319873,  0.03821936, -0.07455685, ..., -0.03109083,
         0.01851494, -0.02415565],
       [ 0.01181482,  0.03402383, -0.08436038, ..., -0.01092477,
         0.00902986, -0.02101252],
       [-0.

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.00336468, -0.01582923, -0.13496248, ..., -0.01464091,
         0.0187047 , -0.01987429],
       [-0.00028355, -0.03545125, -0.11335072, ...,  0.01082898,
         0.00939875, -0.03596351],
       [-0.0139256 , -0.02346371, -0.12028841, ..., -0.0084768 ,
         0.00412895, -0.0082211 ],
       ...,
       [-0.01196215, -0.02523152, -0.11374032, ..., -0.00479451,
         0.01827382, -0.03594762],
       [-0.001994  , -0.02212097, -0.11329624, ...,  0.00403074,
         0.01084058, -0.02355101],
       [-0.02842886, -0.03065255, -0.10247262, ..., -0.00252998,
         0.00715496,  0.00452009]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.04604157, -0.03612845, -0.13570549, ...,  0.03715238,
         0.02212611, -0.02095915],
       [-0.04604449, -0.03607913, -0.13564539, ...,  0.03710367,
         0.02214901, -0.02086223],
       [-0.01564894, -0.01585892, -0.0949917 , ...,  0.01215874,


         0.0174051 , -0.00204895]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[ 0.12305459, -0.09925319, -0.07149488, ..., -0.04033301,
        -0.02763128, -0.03061927],
       [ 0.13058041, -0.10667354, -0.08682529, ..., -0.00548986,
        -0.0145183 , -0.00944214],
       [ 0.11118593, -0.10051947, -0.06880558, ..., -0.01313735,
        -0.02600503, -0.02224466],
       ...,
       [ 0.13545288, -0.12063146, -0.07553969, ...,  0.00235407,
        -0.02836056, -0.00535433],
       [ 0.10447702, -0.08968079, -0.05768637, ..., -0.02445513,
        -0.02640579, -0.02396425],
       [ 0.13556449, -0.09757047, -0.07317001, ..., -0.02164493,
      

        -0.02596334,  0.03204243]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[ 0.09564755, -0.0073897 , -0.05993468, ...,  0.06233278,
        -0.03057592,  0.03226653],
       [ 0.1024583 , -0.01398573, -0.04460723, ...,  0.03723019,
        -0.03258107,  0.0431848 ],
       [ 0.11622906,  0.00502379, -0.04573941, ...,  0.03674926,
        -0.00914796,  0.04949397],
       ...,
       [ 0.09346361, -0.01648558, -0.03789779, ...,  0.03387382,
        -0.02359429,  0.03137541],
       [ 0.09073876, -0.0172087 , -0.03068554, ...,  0.03457737,
        -0.02578977,  0.05600369],
       [ 0.10776065, -0.02699378, -0.04864318, ...,  0.04488152,
        -0.00608929,  0.02642467]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0

...

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.9998979 ,  0.9698462 ,  0.98661613, ..., -0.99715406,
        -0.95281297, -0.9975929 ],
       [-0.9998892 ,  0.96435213,  0.99150544, ..., -0.99689347,
        -0.958558  , -0.9977466 ],
       [-0.99989265,  0.9584886 ,  0.98852   , ..., -0.9969184 ,
        -0.95758355, -0.99727464],
       ...,
       [-0.9998758 ,  0.96256745,  0.99028456, ..., -0.996855  ,
        -0.9620716 , -0.9974853 ],
       [-0.9998959 ,  0.96250093,  0.99040496, ..., -0.99662477,
        -0.95886904, -0.99725527],
       [-0.9998908 ,  0.95720476,  0.99146503, ..., -0.99690706,
        -0.95862395, -0.99717444]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.9999265 ,  0.9623231 ,  0.9841815 , ..., -0.9961675 ,
        -0.9590443 , -0.9977187 ],
       [-0.99992627,  0.962028  ,  0.98422366, ..., -0.9961585 ,
        -0.9587514 , -0.9977073 ],
       [-0.99990743,  0.97068506,  0.99335456, ..., -0.99674004,


        -0.9548216 , -0.99785435]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)>,)
(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.99993294,  0.9663662 ,  0.9915046 , ..., -0.99763036,
        -0.949394  , -0.9978358 ],
       [-0.9998789 ,  0.9626047 ,  0.99127454, ..., -0.9971071 ,
        -0.952842  , -0.99733573],
       [-0.9998873 ,  0.9627306 ,  0.9919447 , ..., -0.9972305 ,
        -0.96820927, -0.9975746 ],
       ...,
       [-0.99986917,  0.9470671 ,  0.9897682 , ..., -0.995504  ,
        -0.96009886, -0.99729276],
       [-0.99990475,  0.9588899 ,  0.98942393, ..., -0.996996  ,
        -0.95607287, -0.99733126],
       [-0.9998766 ,  0.9610796 ,  0.9898805 , ..., -0.9974416 ,
      

(<tf.Tensor: shape=(32, 256), dtype=float32, numpy=
array([[-0.9999197 ,  0.9541487 ,  0.99038213, ..., -0.99663854,
        -0.95789045, -0.99716574],
       [-0.9999049 ,  0.9516551 ,  0.9878007 , ..., -0.9962508 ,
        -0.9660465 , -0.9972784 ],
       [-0.99990404,  0.96532845,  0.9912761 , ..., -0.99733377,
        -0.9626093 , -0.9975441 ],
       ...,
       [-0.99989164,  0.95683765,  0.99076486, ..., -0.99627614,
        -0.96385914, -0.9973549 ],
       [-0.9998908 ,  0.9571929 ,  0.99146205, ..., -0.9969063 ,
        -0.95861673, -0.997173  ],
       [-0.99990475,  0.9631495 ,  0.9910537 , ..., -0.99670815,
        -0.9548163 , -0.9978536 ]], dtype=float32)>,)
epoch 250, perplexity 1014.362734, time 0.53 sec
分开
before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 0.,

        -0.9971849 ]], dtype=float32)>,)
before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[-0.9998834 ,  0.95775837,  0.98966515,  0.9994206 , -0.9984941 ,
         0.99242455, -0.4750363 , -0.05177361,  0.16118596, -0.97355944,
        -0.9144958 , -0.61424905, -0.99711925, -0.9996612 , -0.9970122 ,
         0.9620293 , -0.9962212 ,  0.9948969 , -0.72800696,  0.9229049 ,
         0.99518037, -0.8764943 , -0.9801937 ,  0.9971511 , -0.9976968 ,
        -0.47561014, -0.9962054 , -0.98902595,  0.9985603 , -0.9839696 ,
        -0.99870706,  0.9969904 , -0.9894542 ,  0.997328  , -0.994812  ,
        -0.9990153 ,  0.70840204, -0.9651699 , -0.9993366 , -0.99720836,
        -0.9956496 , -0.9968042 ,  0.886178  ,  0.99167216, -0.08764579,
         0.42783403,  0.9912825 ,  0.9993166 ,  0.9902414 , -0.67836493,
         0.99796814, -0.9970721 ,  0.9966961 ,  0.9911362 , -0.99875474,
         0.9502748 , -0.98423696,  0.98850274, -0.91661185, -0

        -0.9971849 ]], dtype=float32)>,)
before X  (1, 1027)

 reshape X  (1, 1027)
(<tf.Tensor: shape=(1, 256), dtype=float32, numpy=
array([[-0.9998834 ,  0.95775837,  0.98966515,  0.9994206 , -0.9984941 ,
         0.9924246 , -0.47503626, -0.05177355,  0.16118602, -0.97355944,
        -0.9144958 , -0.6142491 , -0.99711925, -0.9996612 , -0.9970122 ,
         0.96202934, -0.9962212 ,  0.9948969 , -0.72800696,  0.9229049 ,
         0.99518037, -0.8764943 , -0.9801937 ,  0.9971511 , -0.9976969 ,
        -0.47561014, -0.9962054 , -0.98902595,  0.99856037, -0.9839696 ,
        -0.99870723,  0.9969903 , -0.9894542 ,  0.997328  , -0.994812  ,
        -0.9990153 ,  0.70840186, -0.9651699 , -0.9993366 , -0.99720836,
        -0.9956496 , -0.9968042 ,  0.886178  ,  0.99167216, -0.08764574,
         0.42783406,  0.9912825 ,  0.9993167 ,  0.9902414 , -0.67836493,
         0.9979681 , -0.9970721 ,  0.9966961 ,  0.991136  , -0.99875474,
         0.95027477, -0.984237  ,  0.98850274, -0.9166119 , -0